In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from scipy import signal 
from keras.models import Sequential
from keras.layers.core import Dense, Activation
import keras
import seaborn as sns
import math
import plotly.plotly as py
import plotly.graph_objs as go
import plotly
from plotly.graph_objs import Surface
from plotly.graph_objs import Scatter3d
plotly.offline.init_notebook_mode(connected=True)


%matplotlib inline

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters
Using TensorFlow backend.


In [2]:
def getNearestValue(row, timeImuList, accelerationList, imuPitchList):
    idx = np.abs(timeImuList-row["time"]).argmin()
    return pd.Series([accelerationList[idx], imuPitchList[idx]])

In [3]:
dfImu= pd.read_csv("imuLongTokyoDistrict.csv")
dfPacmod = pd.read_csv("pacmodLongTokyoDistrict.csv")
dfImu = dfImu.rename(columns={'%time':'time'})
dfPacmod= dfPacmod.rename(columns={'%time':'time'})

In [4]:
dfImu["time"] = dfImu["time"] - dfImu["time"][0]
dfPacmod["time"] = dfPacmod["time"] - dfPacmod["time"][0]
dfImu["time"] = dfImu["time"]/(10**9)
dfPacmod["time"] = dfPacmod["time"]/(10**9)

dfImu["time"] = dfImu["time"] - 0.4 #入力遅れの分の加算

dfImu=dfImu.dropna()
dfPacmod=dfPacmod.dropna()
dfPacmod=dfPacmod[dfPacmod.speed>0] #速度が0のところはとりあえず無視
dfImu["x"] = -1 * dfImu["x"]
dfPacmod["speed"] = (dfPacmod["leftWheelSpeed"] + dfPacmod["rightWheelSpeed"])/2 #車速にwheelSpeedを用いる

numForSpeed=5#移動平均の個数
b=np.ones(numForSpeed)/numForSpeed
dfPacmod["speed"]=np.convolve(dfPacmod["speed"], b, mode='same')#移動平均

deltaT = np.diff(dfPacmod["time"]).mean()
dfPacmod["acc"]=np.insert(np.diff(dfPacmod["speed"])/deltaT, 0, 0)
numForAcc=20#移動平均の個数
b=np.ones(numForAcc)/numForAcc
dfPacmod["accFil"]=np.convolve(dfPacmod["acc"], b, mode='same')#移動平均

In [5]:
b, a = signal.butter(6, 0.1, 'low') #次数6でカットオフ周波数は5Hz
dfImu["acceleration"] = signal.filtfilt(b, a, dfImu["x"])

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/scipy/signal/_arraytools.py:45: FutureWarning:

Using a non-tuple sequence for multidimensional indexing is deprecated; use `arr[tuple(seq)]` instead of `arr[seq]`. In the future this will be interpreted as an array index, `arr[np.array(seq)]`, which will result either in an error or a different result.



In [6]:
imuXList = dfImu["acceleration"]
imuPitchList = dfImu["pitch"]
timeImuList = dfImu["time"]
dfPacmod[["acceleration","pitch"]]=dfPacmod.apply(getNearestValue, timeImuList=timeImuList, accelerationList=imuXList, imuPitchList=imuPitchList, axis=1)

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:2: FutureWarning:

'argmin' is deprecated. Use 'idxmin' instead. The behavior of 'argmin' will be corrected to return the positional minimum in the future. Use 'series.values.argmin' to get the position of the minimum now.



In [7]:
dataPacmod = dfPacmod.copy()
dataPacmod=dataPacmod[abs(dataPacmod.steer) < 0.5]
dataPacmod= dataPacmod[np.abs(dataPacmod.pitch-dataPacmod.pitch.mean())/dataPacmod.pitch.std()<=1]
dataPacmod = dataPacmod.query("0<speed<60 & brake > 0.025 & accFil<-0.7")
dataPacmod["speedKey"]=pd.cut(dataPacmod.speed, 60, labels=[i+1 for i in range(60)])
dataPacmod["brakeKey"]=pd.cut(dataPacmod.brake, 25, labels=[i+1 for i in range(25)])


groupListBrake=list(dataPacmod.groupby(["speedKey", "brakeKey"], as_index=False).groups.keys())
dataPacmod["groupBrake"] = dataPacmod.apply(lambda row : groupListBrake.index((row["speedKey"], row["brakeKey"])), axis=1)

indexSort=np.argsort(dataPacmod.groupby("groupBrake").count().time.values)[::-1]
valueSort=np.sort(dataPacmod.groupby("groupBrake").count().time.values)[::-1]

#numMed = np.median(valueSort)
numMed=30

i=0
while True:
    if valueSort[i]-int(numMed)>0:
        dataPacmod.drop(dataPacmod[dataPacmod.groupBrake==indexSort[i]].sample(n=valueSort[i]-int(numMed)).index, inplace=True)
        i=i+1
    else:
        break

In [8]:
groupBrakeMeanList=dataPacmod.groupby("groupBrake").mean()["accFil"].values
groupBrakeStdList=dataPacmod.groupby("groupBrake").std(ddof=0)["accFil"].values
def removeOutliers(row):
    #1を外れ値とする
    stddev=groupBrakeMeanList[row.groupBrake]
    mean=groupBrakeMeanList[row.groupBrake]
        
    if stddev==0.0: #データが1個しかないとき
        return 0
    
    elif np.abs(row["accFil"]-mean)/stddev>1:
        return 1
    
    else:
        return 0
    
dataPacmod["remove"]=dataPacmod.apply(removeOutliers, axis=1)

In [9]:
dfRemove=dataPacmod[dataPacmod.remove==0]

speedList = dfRemove.groupby("groupBrake").mean()["speed"].values
accList= dfRemove.groupby("groupBrake").mean()["accFil"].values
brakeList = dfRemove.groupby("groupBrake").mean()["brake"].values

scatter = Scatter3d(x=dataPacmod.speed, y=dataPacmod.brake, z=dataPacmod.accFil, mode='markers',marker=dict(size=2, color="red"), name="raw")
scatterRemove = Scatter3d(x=dfRemove.speed, y=dfRemove.brake, z=dfRemove.accFil, mode='markers',marker=dict(size=3, color="blue"), name="RemoveOutliers")
scatterBoss = Scatter3d(x=speedList, y=brakeList, z=accList, mode='markers',marker=dict(size=2, color="green"), name="Boss")
layout = go.Layout(title="BrakeModel", scene=dict(xaxis=dict(title="speed",range=[0, 60]), yaxis=dict(title="brake"), zaxis=dict(title="acceleration",)))
fig = go.Figure(data=[scatter,scatterRemove, scatterBoss], layout=layout)
plotly.offline.iplot(fig)
#plotly.offline.plot(fig, filename='/home/ubuntu/brake.html')

In [10]:
dataPacmodTrain = dataPacmod[dataPacmod["remove"]==0]
dataPacmodTrain=dataPacmodTrain.query("speed>8")
minNum=dataPacmodTrain["accFil"].min()
maxNum=dataPacmodTrain["accFil"].max()
x_train=np.array([dataPacmodTrain["speed"]/dataPacmodTrain["speed"].max(), dataPacmodTrain["brake"]]).T
y_train=(dataPacmodTrain["accFil"].values-minNum)/(maxNum-minNum)

In [11]:
model = Sequential()
model.add(Dense(64, input_dim=2, activation='sigmoid'))
model.add(Dense(64, activation='sigmoid'))
model.add(Dense(64, activation='sigmoid'))
model.add(Dense(1, activation='linear'))
model.compile(optimizer="Adam", loss="mean_squared_error")

#earlyStopping=keras.callbacks.EarlyStopping(monitor='val_loss', patience=0, verbose=1, mode='auto')
model.fit(x_train, y_train, batch_size=128, epochs=300, verbose=1, validation_split=0.2, shuffle=True)

Train on 8702 samples, validate on 2176 samples
Epoch 1/300
8702/8702 [==============================] - 1s 131us/step - loss: 0.0397 - val_loss: 0.0421
Epoch 2/300
8702/8702 [==============================] - 0s 33us/step - loss: 0.0386 - val_loss: 0.0420
Epoch 3/300
8702/8702 [==============================] - 0s 32us/step - loss: 0.0372 - val_loss: 0.0437
Epoch 4/300
8702/8702 [==============================] - 0s 31us/step - loss: 0.0346 - val_loss: 0.0359
Epoch 5/300
8702/8702 [==============================] - 0s 32us/step - loss: 0.0293 - val_loss: 0.0278
Epoch 6/300
8702/8702 [==============================] - 0s 33us/step - loss: 0.0216 - val_loss: 0.0189
Epoch 7/300
8702/8702 [==============================] - 0s 32us/step - loss: 0.0135 - val_loss: 0.0123
Epoch 8/300
8702/8702 [==============================] - 0s 32us/step - loss: 0.0094 - val_loss: 0.0091
Epoch 9/300
8702/8702 [==============================] - 0s 32us/step - loss: 0.0083 - val_loss: 0.0084
Epoch 10/300
87

8702/8702 [==============================] - 0s 32us/step - loss: 0.0034 - val_loss: 0.0043
Epoch 79/300
8702/8702 [==============================] - 0s 33us/step - loss: 0.0033 - val_loss: 0.0041
Epoch 80/300
8702/8702 [==============================] - 0s 32us/step - loss: 0.0033 - val_loss: 0.0034
Epoch 81/300
8702/8702 [==============================] - 0s 32us/step - loss: 0.0033 - val_loss: 0.0041
Epoch 82/300
8702/8702 [==============================] - 0s 32us/step - loss: 0.0034 - val_loss: 0.0031
Epoch 83/300
8702/8702 [==============================] - 0s 33us/step - loss: 0.0033 - val_loss: 0.0032
Epoch 84/300
8702/8702 [==============================] - 0s 32us/step - loss: 0.0033 - val_loss: 0.0039
Epoch 85/300
8702/8702 [==============================] - 0s 32us/step - loss: 0.0034 - val_loss: 0.0037
Epoch 86/300
8702/8702 [==============================] - 0s 33us/step - loss: 0.0034 - val_loss: 0.0031
Epoch 87/300
8702/8702 [==============================] - 0s 32us/st

8702/8702 [==============================] - 0s 31us/step - loss: 0.0030 - val_loss: 0.0028
Epoch 156/300
8702/8702 [==============================] - 0s 33us/step - loss: 0.0032 - val_loss: 0.0034
Epoch 157/300
8702/8702 [==============================] - 0s 31us/step - loss: 0.0031 - val_loss: 0.0028
Epoch 158/300
8702/8702 [==============================] - 0s 33us/step - loss: 0.0031 - val_loss: 0.0033
Epoch 159/300
8702/8702 [==============================] - 0s 32us/step - loss: 0.0031 - val_loss: 0.0034
Epoch 160/300
8702/8702 [==============================] - 0s 32us/step - loss: 0.0032 - val_loss: 0.0028
Epoch 161/300
8702/8702 [==============================] - 0s 33us/step - loss: 0.0032 - val_loss: 0.0029
Epoch 162/300
8702/8702 [==============================] - 0s 32us/step - loss: 0.0031 - val_loss: 0.0034
Epoch 163/300
8702/8702 [==============================] - 0s 32us/step - loss: 0.0031 - val_loss: 0.0030
Epoch 164/300
8702/8702 [==============================] - 0

8702/8702 [==============================] - 0s 32us/step - loss: 0.0031 - val_loss: 0.0032
Epoch 233/300
8702/8702 [==============================] - 0s 33us/step - loss: 0.0030 - val_loss: 0.0032
Epoch 234/300
8702/8702 [==============================] - 0s 32us/step - loss: 0.0030 - val_loss: 0.0027
Epoch 235/300
8702/8702 [==============================] - 0s 33us/step - loss: 0.0031 - val_loss: 0.0029
Epoch 236/300
8702/8702 [==============================] - 0s 32us/step - loss: 0.0031 - val_loss: 0.0033
Epoch 237/300
8702/8702 [==============================] - 0s 32us/step - loss: 0.0031 - val_loss: 0.0033
Epoch 238/300
8702/8702 [==============================] - 0s 32us/step - loss: 0.0031 - val_loss: 0.0027
Epoch 239/300
8702/8702 [==============================] - 0s 33us/step - loss: 0.0032 - val_loss: 0.0030
Epoch 240/300
8702/8702 [==============================] - 0s 32us/step - loss: 0.0030 - val_loss: 0.0030
Epoch 241/300
8702/8702 [==============================] - 0

In [12]:
speed_test = np.arange(0, 80, 1)
accel_test=np.arange(0, 1.0, 0.01)
X, Y = np.meshgrid(speed_test, accel_test)

predict=[]
for i in range(0, 100):
    predict.append(model.predict(np.array([X[i]/X[i].max(), Y[i]]).T))
    
Z=np.array(predict).reshape(100, 80)

surface = Surface(x=X, y=Y, z=Z*(maxNum-minNum)+minNum, colorscale='coolwarm', name="predictSurface")
scatterBoss = Scatter3d(x=speedList, y=brakeList, z=accList, mode='markers',marker=dict(size=2, color="green"), name="Boss")
layout = go.Layout(title="BrakeModel", scene=dict(xaxis=dict(title="speed",range=[80, 0]), yaxis=dict(title="CMD",range=[0.1, 0.7]), zaxis=dict(title="acceleration",range=[-10, 0])))
fig = go.Figure(data=[surface, scatterBoss], layout=layout)
plotly.offline.iplot(fig)
plotly.offline.plot(fig, filename='/home/ubuntu/BrakeModel.html')

'file:///home/ubuntu/BrakeModel.html'